In [ ]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib osx

# 1. Diamond Square Algorithm
https://en.wikipedia.org/wiki/Diamond-square_algorithm
- Fixed boundary conditions result in a very smooth terrain; periodic boundary conditions have the same initial
value for all 4 corners

In [ ]:
# terrain size must be square, with width & height 2**n + 1

# periodic averaging 
def periodic_square(arr, x, y, step, h):
    n = arr.shape[0] - 1
    rand = np.random.uniform(-h, h)
    total = (arr[(y-step)%n,x%n] + arr[(y+step)%n,x%n] + arr[y,(x+step)%n] + arr[y,(x-step)%n])/4.0
    return total + rand

def periodic_diamond(arr, x, y, step, h):
    n = arr.shape[0] - 1
    rand = np.random.uniform(-h, h)
    total = (arr[(y-step)%n,(x-step)%n] + arr[(y+step)%n,(x+step)%n] + 
             arr[(y-step)%n,(x+step)%n] + arr[(y+step)%n,(x-step)%n])/4.0
    return total + rand

# define diamond step
def diamond(arr, h):
    """
    arr (2d np.array) : n x n array
    Sets the midpoint of the square array to the average of the 4 corners + a random value
    """
    # Each random value is multiplied by a scale constant, which decreases with each iteration; 0.0 <= h <= 1.0
    n = arr.shape[0]
    
    # d = (n - 1)//2**iteration : distance from one updated cell to next
    # step = distance from one cell to boundaries used to update
    step = d//2
    
    for y in range(step, n, d):
        for x in range(step, n, d):
            # left = x-d, right = x+d, down = y+d, up = y-d
            # fixed boundary conditions: 
            # mid_val = (arr[y-step,x-step] + arr[y-step,x+step] + 
            #            arr[y+step,x-step] + arr[y+step,x+step])/4.0 + np.random.rand()
            mid_val = periodic_diamond(arr, x, y, step, h) # periodic conditions
            arr[y, x] = mid_val
    

# define square step
def square(arr, d, h):
    # d = distance from one point to the endpoints used to average
    step = d//2
    
    # columns
    for y in range(0, n, d):
        for x in range(step, n, d):
            # arr[y, x] = square_helper(arr, x, y, step, h) # fixed conditions
            arr[y, x] = periodic_square(arr, x, y, step, h)
    
    # rows    
    for y in range(step, n, d):
        for x in range(0, n, d):
            # arr[y, x] = square_helper(arr, x, y, step, h) # fixed conditions
            arr[y, x] = periodic_square(arr, x, y, step, h)
            
    
def square_helper(arr, x, y, step, h):
    """
    Returns the square step for a single cell [y, x] for fixed boundary conditions.
    """
    # take 4 ordinal directions:
    total, num = 0, 0.0 # sum & num of directions that were added
    # up: if y != 0:
    if y != 0:
        total += arr[y-step, x]
        num += 1
    # down: if y coord != m-1:
    if y != n-1:
        total += arr[y+step, x]
        num += 1
    # left: if x coord != 0:
    if x != 0:
        total += arr[y, x-step]
        num += 1
    # right: if x coord != n-1:
    if x != n-1:
        total += arr[y, x+step]
        num += 1

    rand = np.random.uniform(-h, h)
    return total/num + rand

**Set the random seed for consistent results (optional):**

In [ ]:
np.random.seed(2023)

# 2. Build Terrains to Erode

In [ ]:
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [ ]:
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    return fig

def update_build(contour=False):
    plt.clf()
    ax1 = fig.add_subplot(121,projection='3d')
    
    ax1.set_xlim3d(0, n)
    ax1.set_ylim3d(0, n)
    ax1.set_zlim3d(np.min(Z), np.max(Z))

    ax1.set_title('Surface Relief')
    surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
            antialiased=False,linewidth=0)

    ax2 = fig.add_subplot(122,aspect='equal')
    ax2.set_title('Elevation')

    im = ax2.pcolor(Z,cmap=cm.terrain)
    if contour:
        cs = ax2.contour(Z,6,colors='k')

    # Add a color bar which maps values to colors.
    cbar = fig.colorbar(im, shrink=0.5, aspect=5)
    # Add the contour line levels to the colorbar
    if contour:
        cbar.add_lines(cs)

    #plt.show()
    plt.draw()
    plt.pause(0.02)
    
    
def update_erosion(contour=False):
    plt.clf()
    ax1 = fig.add_subplot(121,projection='3d')

    ax1.set_xlim3d(0, NX)
    ax1.set_ylim3d(0, NY)
    ax1.set_zlim3d(min_height, max_height) # fixed z axis
    
    
    ZPlot = np.copy(Z)
    ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
    ZPlot -= ls.ZBeachLevel

    ax1.set_title('Surface Relief')
    surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
            antialiased=False,linewidth=0)

    ax2 = fig.add_subplot(122,aspect='equal')
    ax2.set_title('Elevation')

    im = ax2.pcolor(ZPlot,cmap=cm.terrain)
    if contour:
        cs = ax2.contour(ZPlot,6,colors='k')

    # Add a color bar which maps values to colors.
    cbar = fig.colorbar(im, shrink=0.5, aspect=5)
    # Add the contour line levels to the colorbar
    if contour:
        cbar.add_lines(cs)

    plt.draw()
    plt.pause(0.2)  

### Animating (no saving)

In [ ]:
n = 2**8 + 1 
d = n - 1
h = 1
dh = 0.5
arr = np.zeros((n, n))
arr[0,0] = 1
arr[-1,0] = 1
arr[0,-1] = 1
arr[-1,-1] = 1

m, n = np.shape(arr)
y, x = np.arange(m), np.arange(n)
X, Y = np.meshgrid(y, x)
Z = arr

fig = init_figure()

while d >= 1:
    diamond(arr, h)
    square(arr, d, h)
    
    d = d//2
    h *= dh
    # min_height, max_height = np.min(arr), np.max(arr)
    
    update_build()

update_build(contour=True)

## Animating (with saving)

In [ ]:
from matplotlib.animation import FFMpegWriter

In [ ]:
metadata = dict(title='Diamond Square build', artist='Matplotlib',comment='Diamond square build.')
writer = FFMpegWriter(fps=1, metadata=metadata,bitrate=200000)

In [ ]:
n = 2**8 + 1 
d = n - 1
h = 1
dh = 0.5
arr = np.zeros((n, n))
arr[0,0] = 1
arr[-1,0] = 1
arr[0,-1] = 1
arr[-1,-1] = 1

m, n = np.shape(arr)
y, x = np.arange(m), np.arange(n)
X, Y = np.meshgrid(y, x)
Z = arr

fig = init_figure()

with writer.saving(fig, "build.mp4", dpi=200):
    while d >= 1:
        diamond(arr, h)
        square(arr, d, h)

        d = d//2
        h *= dh

        update_build()
        writer.grab_frame()

    update_build(contour=True)
    writer.grab_frame()


# 3. Erode Terrains
Source: EPS109 Homework 9

In [ ]:
from landscapeWithOcean import LandscapeWithOcean

In [ ]:
### Physical Parameters
K = 1.0e-6 # meters^(1-2m)/yr

D = 0.005 # m^2/yr

# uplift rate
uplift = 0 # if we are eroding down to the ocean, ignore uplift

dist = 9
dx = dist
dy = dist

### Model parameters

# Set the time step dt using eta = D * dt / dx^2 <= 1/8
# dt <= dx^2 / D * 8
dt = dist**2 / (D * 8)
print('dt[years] =',dt)

#Area exponent A^m, default m=1
a=1

#gradient exponent g^n, default n=1
g=1.5 

#erosion threshold 
theta_c = 10

# Total simulation time
T = 2e6 # 2 million years

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of iterations:',n_iter)

#### Generate terrain to erode:

In [ ]:
n = 2**7 + 1 
d = n - 1
h = 1
dh = 0.5
arr = np.zeros((n, n))
arr[0,0] = 0.5
arr[-1,0] = 0.5
arr[0,-1] = 0.5
arr[-1,-1] = 0.5

m, n = arr.shape
y, x = np.arange(m), np.arange(n)
X, Y = np.meshgrid(y, x)
Z = arr

while d >= 1:
    diamond(arr, h)
    square(arr, d, h)
    
    d = d//2
    h *= dh

#### Convert to landscape for erosion process:

In [ ]:
NY, NX = arr.shape
Z = Z.T # transpose for erosion methods
min_height, max_height = np.min(Z), np.max(Z) # for fixed z-axis when graphing

oceanLevelParameter = 0.1 # 10% of max height is considered ocean level
ls = LandscapeWithOcean(NX,NY)
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)
ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

In [ ]:
fig = init_figure()
Znew = np.copy(Z)

# with writer.saving(fig, 'erosion.mp4', dpi=200): # uncomment and indent code below if saving animation
for it in range(1,n_iter+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe periodic boundary conditions.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**a * gradient**g - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * (ls.A[i,j]**a * gradient**g - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ((Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2)

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_erosion()
            # writer.grab_frame() # uncomment if saving animation
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

update_erosion()
print(' Simulation finished.')